# **\[SOLAR\]** SIMULATION (DCRNN)

JiyunLim  
2020-12-12

## Data

In [1]:
import pandas as pd
import numpy as np
import os

In [2]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

## DCRNN

In [2]:
%run model/dcrnn

In [3]:
s6 = Simulator()

In [4]:
class DC_RNN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(DC_RNN, self).__init__()
        self.recurrent = DCRNN(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [ ]:
s6.simulate(
    n_iteration = 30,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = DC_RNN
)

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## RSLT

In [ ]:
df_ = pd.concat([pd.read_csv(fname) for fname in fnames]).reset_index(drop=True)

In [ ]:
df_

In [ ]:
df_.groupby(by=['model','method']).agg({'mse':[np.mean, np.std]})